In [1]:
import pandas as pd
import numpy as np
import re

In [105]:
pd.set_option("display.max_colwidth", 50)
pd.set_option("display.max_rows", 20)

In [2]:
businesses = pd.read_pickle('grouped_ca.p')

In [10]:
florida = pd.read_csv("florida_review_data.csv")

In [62]:
addrs = ['1270 Picador Blvd Ste E-A San Diego, CA, 92154',
         '1270 Picador Blvd Unit 108A San Diego, CA, 92154',
         '1510 Front St # 204, CA, 92101',
         '645 H St #C Chula Vista, CA, 91910',
         '1270 Picador Blvd Studio E-B San Diego, CA, 92154']
for a in addrs:
    match = re.search(r'(?:ste|unit)\W+([\w-]+)\W', a.lower())
    if match:
        print(match.groups(0)[0])
    match = re.search(r'studio\W+([\w-]+)\W', a.lower())
    if match:
        print(match.groups(0)[0])
    match = re.search(r'#\W*([\w-]+)\W', a.lower())
    if match:
        print(match.groups(0)[0])

e-a
108a
204
c
e-b


In [109]:
regs = [r'(?:ste|unit)\W+([\w-]+)\W',
       r'studio\W+([\w-]+)\W',
       r'#\W*([\w-]+)\W']
def stringify_key(row):
    lat_lon_pair = "{:.5f}".format(row.lat) + ":" + "{:.5f}".format(row.lon) + "#"
    address = row.address.lower()
    for reg in regs:
        match = re.search(reg, address)
        if match:
            return lat_lon_pair + match.groups(0)[0]
    return lat_lon_pair
    

In [92]:
businesses['norm_id'] = businesses.apply(stringifyKey, axis=1)

In [93]:
businesses = businesses.explode('norm_id')

In [94]:
def fuzzy_latlon(df, epsilon=0.0001):
    df_new = df.sort_values(by=['lat','lon'])
    df_new = df_new.reset_index().drop(["index"], axis = 1)
    g_id = 0
    df_new['g_id'] = -1
    j = 0
    for i in range(len(df) - 1):
        if i >= j:
            old = df_new.iloc[i]['lat_lon']
            df_new.at[i, 'g_id'] = g_id
            j = i + 1
            while similar(df_new.iloc[j]['lat_lon'],old,epsilon):
                df_new.at[j, 'g_id'] = g_id
                j += 1
            g_id += 1
    return df_new

def similar(t1, t2, epsilon):
    diff1 = abs(t1[0] - t2[0])
    diff2 = abs(t1[1] - t2[1])
    if (diff1 <= epsilon) and (diff2 <= epsilon):
        return True
    else:
        return False

In [98]:
df = pd.read_pickle('review_features.p')

address       lat  \
0                 8000 Sunset Blvd Ste 19 Salon Republic, CA, 90046  34.09771   
1                 8000 Sunset Blvd Ste 19 Salon Republic, CA, 90046  34.09771   
2                 8000 Sunset Blvd Ste 19 Salon Republic, CA, 90046  34.09771   
3                 8000 Sunset Blvd Ste 19 Salon Republic, CA, 90046  34.09771   
4                 8000 Sunset Blvd Ste 19 Salon Republic, CA, 90046  34.09771   
5                 8000 Sunset Blvd Ste 19 Salon Republic, CA, 90046  34.09771   
6                 8000 Sunset Blvd Ste 19 Salon Republic, CA, 90046  34.09771   
7                 8000 Sunset Blvd Ste 19 Salon Republic, CA, 90046  34.09771   
8                 8000 Sunset Blvd Ste 19 Salon Republic, CA, 90046  34.09771   
9                 8000 Sunset Blvd Ste 19 Salon Republic, CA, 90046  34.09771   
10                8000 Sunset Blvd Ste 19 Salon Republic, CA, 90046  34.09771   
11                8000 Sunset Blvd Ste 19 Salon Republic, CA, 90046  34.09771   
12                8000 Sunset Blvd Ste 19 Salon Republic, CA, 90046  34.09771   
13                8000 Sunset Blvd Ste 19 Salon Republic, CA, 90046  34.09771   
14                8000 Sunset Blvd Ste 19 Salon Republic, CA, 90046  34.09771   
15                8000 Sunset Blvd Ste 19 Salon Republic, CA, 90046  34.09771   
16                8000 Sunset Blvd Ste 19 Salon Republic, CA, 90046  34.09771   
17                8000 Sunset Blvd Ste 19 Salon Republic, CA, 90046  34.09771   
18                8000 Sunset Blvd Ste 19 Salon Republic, CA, 90046  34.09771   
19                8000 Sunset Blvd Ste 19 Salon Republic, CA, 90046  34.09771   
20                                    7268 W Sunset Blvd, CA, 90046  34.09780   
21                                    7268 W Sunset Blvd, CA, 90046  34.09780   
22                                    7268 W Sunset Blvd, CA, 90046  34.09780   
23                                    7268 W Sunset Blvd, CA, 90046  34.09780   
24                                    7268 W Sunset Blvd, CA, 90046  34.09780   
25                                    7268 W Sunset Blvd, CA, 90046  34.09780   
26                                    7268 W Sunset Blvd, CA, 90046  34.09780   
27                                    7268 W Sunset Blvd, CA, 90046  34.09780   
28                                    7268 W Sunset Blvd, CA, 90046  34.09780   
29                                    7268 W Sunset Blvd, CA, 90046  34.09780   
30                                    7268 W Sunset Blvd, CA, 90046  34.09780   
31                                    7268 W Sunset Blvd, CA, 90046  34.09780   
32                                    7268 W Sunset Blvd, CA, 90046  34.09780   
33                                    7268 W Sunset Blvd, CA, 90046  34.09780   
34                                    7268 W Sunset Blvd, CA, 90046  34.09780   
35                                    7268 W Sunset Blvd, CA, 90046  34.09780   
36                                    7268 W Sunset Blvd, CA, 90046  34.09780   
37                                    7268 W Sunset Blvd, CA, 90046  34.09780   
38                                    7268 W Sunset Blvd, CA, 90046  34.09780   
39                                    7268 W Sunset Blvd, CA, 90046  34.09780   
40                                      1218 Irvine Blvd, CA, 92780  33.74603   
41                                      1218 Irvine Blvd, CA, 92780  33.74603   
42                                      1218 Irvine Blvd, CA, 92780  33.74603   
43                                      1218 Irvine Blvd, CA, 92780  33.74603   
44       8000 Sunset Blvd Ste 58 Salon Christopher Corum, CA, 90046  34.09771   
45       8000 Sunset Blvd Ste 58 Salon Christopher Corum, CA, 90046  34.09771   
46       8000 Sunset Blvd Ste 58 Salon Christopher Corum, CA, 90046  34.09771   
47       8000 Sunset Blvd Ste 58 Salon Christopher Corum, CA, 90046  34.09771   
48       8000 Sunset Blvd Ste 58 Salon Christopher Corum, CA, 90046  34.09771   
49       8

In [101]:
sub = df.iloc[:1000].copy()
sub.columns


Index(['address', 'lat', 'lon', 'name', 'range_days', 'review', 'rubmaps',
       'yelp', 'lat_lon', 'HT_bi_0_count', 'HT_bi_1_count', 'HT_bi_2_count',
       'HT_tri_0_count', 'HT_tri_1_count', 'HT_tri_2_count', 'HT_uni_0_count',
       'HT_uni_1_count', 'HT_uni_2_count', 'sex_bi_0_count', 'sex_bi_1_count',
       'sex_bi_2_count', 'sex_tri_0_count', 'sex_tri_1_count',
       'sex_tri_2_count', 'sex_uni_0_count', 'sex_uni_1_count',
       'sex_uni_2_count'],
      dtype='object')

In [102]:
fuz = fuzzy_latlon(df)
grouped = fuz.groupby(['g_id']).agg({"lat":'max', "lon":'max'})

In [103]:
fuz_with_ids = pd.merge(fuz, grouped, on='g_id').drop(['lat_x', 'lon_x'], axis=1).rename(columns={''})

In [107]:
fuz_with_ids = fuz_with_ids.drop(['lat_x', 'lon_x'], axis=1).rename(columns={'lat_y':'lat', 'lon_y':'lon'})

In [110]:
fuz_with_ids['norm_id'] = fuz_with_ids.apply(stringify_key, axis=1)

In [117]:
real_grouped = fuz_with_ids.groupby('norm_id').agg({"yelp": "sum",
                                  "rubmaps":"sum", "name": lambda x: list(set(x)),
                                     "address":lambda x: list(set(x)),
                                     'HT_bi_0_count':"max",
       'HT_bi_1_count':"max", 'HT_bi_2_count':"max", 'HT_tri_0_count':"max", 'HT_tri_1_count':"max",
       'HT_tri_2_count':"max", 'HT_uni_0_count':"max", 'HT_uni_1_count':"max", 'HT_uni_2_count':"max",
       'sex_bi_0_count':"max", 'sex_bi_1_count':"max", 'sex_bi_2_count':"max", 'sex_tri_0_count':"max",
       'sex_tri_1_count':"max", 'sex_tri_2_count':"max", 'sex_uni_0_count':"max",
       'sex_uni_1_count':"max", 'sex_uni_2_count':"max"})

In [118]:
fuz_with_ids.to_pickle("ca_reviews_with_norm_id.p")

In [119]:
real_grouped.to_pickle("grouped_on_norm_id.p")

In [4]:
norm_id_df = pd.read_pickle('ca_reviews_with_norm_id.p')
feat1_df = pd.read_pickle('ca_features_1.p')

In [25]:
# + 2 * row['HT_uni_2_count']
feat1_df.columns

Index(['address', 'name', 'range_days', 'review', 'rubmaps', 'yelp',
       'HT_bi_0_count', 'HT_bi_1_count', 'HT_bi_2_count', 'HT_tri_0_count',
       'HT_tri_1_count', 'HT_tri_2_count', 'HT_uni_0_count', 'HT_uni_1_count',
       'HT_uni_2_count', 'sex_bi_0_count', 'sex_bi_1_count', 'sex_bi_2_count',
       'sex_tri_0_count', 'sex_tri_1_count', 'sex_tri_2_count',
       'sex_uni_0_count', 'sex_uni_1_count', 'sex_uni_2_count', 'lat', 'lon',
       'norm_id', 'cluster'],
      dtype='object')

In [28]:
#feat1_df['name'] = feat1_df['name'].apply(lambda x: x.lower())
feat1_df['HT_total_score'] = feat1_df.apply(lambda row: row['HT_uni_1_count'] + 2 * row['HT_uni_2_count'], axis=1)

In [30]:
feat1_df[feat1_df['name'] == 'apple spa massage']['review'].iloc[8]#[['review','HT_total_score']]

'stated went see jenny seen quite while greeted with open arms gentle kiss told awhile said yes good see you asked available said new girl want tell is nice get know well contact try new girls so call fake want really went down ask jenny new girl gives good massage like get good massage well fs assured girl great hands right issue like little bit oil use any so work out kinks felt great course came light touch conversation tip wanted im sure jenny told im regular removed red dress blue gstring nice body great breasts typical asian ass lol second time ive done laying stomach put feet breast get nipples hard candy exact thing go back read review her so anyway ran hair back ass boys used tongue back ass scrotum woman loves shows told turn laid side next leaned gave passionate kiss move head breast got lick suck nipples so said started heading south border lol kitty trimmed unfortunately maybe day two old little prickly lol ended licking thing toes curl knew pulling towards her he grabbed 

In [43]:
pd.set_option('display.max_columns', 100)

In [53]:
feat1_df[feat1_df['name'] == 'tui na center']['review'].iloc[-1]#[['review','HT_total_score']]

'hear said today first day location came los angelas usa 7 years know awesome short hwp nice c head lights nice round tight butt speaks good english beautiful face friendly really sweet gal massage good far went got busy things time finish massage turned inside outhe thats easy with happen older guy nice able communicate with little problem nice tat want say case wants change name do covered clothing'